<a href="https://colab.research.google.com/github/CaptainJimbo/MyPortfolio/blob/main/musicGenerator.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [52]:
# Import all remaining packages
import tensorflow as tf
import numpy as np
import os
import time
import functools
from IPython import display as ipythondisplay
from tqdm import tqdm
import subprocess
from IPython.display import Audio
!apt-get install abcmidi timidity > /dev/null 2>&1
!apt-get install -y abcmidi timidity
!pip install pydub
!pip install IPython

# Check that we are using a GPU, if not switch runtimes
#   using Runtime > Change Runtime Type > GPU
#assert len(tf.config.list_physical_devices('GPU')) > 0

!wget -O music.abc "https://dl.dropboxusercontent.com/scl/fi/xyvgohdnz73uy0akyolsb/input.abc?rlkey=lcpg5bp57n46d7129qjprgnuy"


Reading package lists... Done
Building dependency tree       
Reading state information... Done
abcmidi is already the newest version (20200122-1).
timidity is already the newest version (2.14.0-8build1).
0 upgraded, 0 newly installed, 0 to remove and 15 not upgraded.
--2023-07-14 21:28:59--  https://dl.dropboxusercontent.com/scl/fi/xyvgohdnz73uy0akyolsb/input.abc?rlkey=lcpg5bp57n46d7129qjprgnuy
Resolving dl.dropboxusercontent.com (dl.dropboxusercontent.com)... 162.125.6.15, 2620:100:6019:15::a27d:40f
Connecting to dl.dropboxusercontent.com (dl.dropboxusercontent.com)|162.125.6.15|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1751713 (1.7M) [text/plain]
Saving to: ‘music.abc’

music.abc           100%[===================>]   1.67M  --.-KB/s    in 0.01s   

2023-07-14 21:28:59 (141 MB/s) - ‘music.abc’ saved [1751713/1751713]



In [ ]:
# using open function isnide a with statement so that the file gets closed afterreading
with open('music.abc', 'r') as file:
    data = file.read()
songs = data.split('\n\n\n')
song[1]

In [43]:
songs = data.split('\n\n\n')
print(f'There are {len(songs)} songs in the file')

There are 4097 songs in the file


In [41]:
data.split('\n\n\n')[0]

'X: 1\nT: The Enchanted Valley\nM: 2/4\nL: 1/16\nB: "O\'Neill\'s 1"\nN: "Very slow" "collected by J. O\'Neill"\nN:\nZ: "Transcribed by Norbert Paap, norbertp@bdu.uva.nl"\nZ:\nK:Gm\nG3-A (Bcd=e) | f4 (g2dB) | ({d}c3-B) G2-E2 | F4 (D2=E^F) |\nG3-A (Bcd=e) | f4 d2-f2 | (g2a2 b2).g2 | {b}(a2g2 f2).d2 |\n(d2{ed}c2) B2B2 | (A2G2 {AG}F2).D2 | (GABc) (d2{ed}c>A) | G2G2 G2z ||\nG | B2c2 (dcAB) | G2G2 G3G | B2d2 (gfdc) | d2g2 (g3ga) |\n(bagf) (gd)d>c | (B2AG) F-D.D2 | (GABc) d2d2 | (bgfd) cA.F2 |\nG2A2 (B2{cB}AG) | A3-G F2-D2 | (GABc) (d2{ed}c>A) | G2G2 G2z2 ||'

In [70]:
def play(song):
  # writing the song to a new ABC file
  with open('song.abc', 'w') as file:
      file.write(song)
  # converting ABC to MIDI using subprocess
  subprocess.run(["abc2midi", "song.abc", "-o", "song.midi"])
  # converting MIDI to WAV
  subprocess.run(["timidity", "song.midi", "-Ow", "-o", "song.wav"])
  # load and play the audio file
  audio = Audio("song.wav")
  print(song)
  return audio


In [71]:
play(songs[0])

X: 1
T: The Enchanted Valley
M: 2/4
L: 1/16
B: "O'Neill's 1"
N: "Very slow" "collected by J. O'Neill"
N:
Z: "Transcribed by Norbert Paap, norbertp@bdu.uva.nl"
Z:
K:Gm
G3-A (Bcd=e) | f4 (g2dB) | ({d}c3-B) G2-E2 | F4 (D2=E^F) |
G3-A (Bcd=e) | f4 d2-f2 | (g2a2 b2).g2 | {b}(a2g2 f2).d2 |
(d2{ed}c2) B2B2 | (A2G2 {AG}F2).D2 | (GABc) (d2{ed}c>A) | G2G2 G2z ||
G | B2c2 (dcAB) | G2G2 G3G | B2d2 (gfdc) | d2g2 (g3ga) |
(bagf) (gd)d>c | (B2AG) F-D.D2 | (GABc) d2d2 | (bgfd) cA.F2 |
G2A2 (B2{cB}AG) | A3-G F2-D2 | (GABc) (d2{ed}c>A) | G2G2 G2z2 ||


In [83]:
vocab = sorted(set(data))
print(f'Vocabulary of the data file, i.e. chords, notes and others',''.join(vocab))

Vocabulary of the data file, i.e. chords, notes and others 	
 !"#%&'()*+,-./0123456789:;<=>?@ABCDEFGHIJKLMNOPQRSTUVWXYZ[\]^_abcdefghijklmnopqrstuvwxyz{|}~


In [115]:
# the algorithm doesnt understand characters it understands pure number i.e. math
# so I transform the characters to indices
# dictionary to map characters to idxs
ch_to_idx = {char:idx for idx,char in enumerate(vocab)}
# encode function to transform strings to list of idxs
encode = lambda string: [ch_to_idx[s] for s in string]
# dictionary to map idxs to characters
idx_to_ch = {idx:char for idx,char in enumerate(vocab)}
# decode function to transform a ist of idxs to a string
decode = lambda digits: ''.join(idx_to_ch[d] for d in digits)

In [123]:
#encode('Hello There'), decode(encode('Hello There'))

In [134]:
batch_size = 4
block_size = 20
vocab_size = len(vocab)
def get_batch(encoded_songs):
  # string has length of len-1 because it starts from 0th place we need n
  n = len(encoded_songs) - 1
  # randomly choose the starting indices for the examples in the training batch
  rnd_idxs = np.random.choice(n-block_size, batch_size)
  input_batch = [encoded_songs[i:i+block_size] for i in rnd_idxs]
  output_batch = [encoded_songs[i+1:i+block_size+1] for i in rnd_idxs]
  # x_batch, y_batch provide the true inputs and targets for network training
  x_batch = np.reshape(input_batch, [batch_size, block_size])
  y_batch = np.reshape(output_batch, [batch_size, block_size])
  return x_batch, y_batch

In [139]:
batch_size = 4
block_size = 20
get_batch(encode(data))[0]

array([[17, 19, 26, 22, 64, 74, 67, 15, 65, 66, 67,  4, 31,  2, 17, 19,
        26, 22, 64, 74],
       [67, 82, 73, 66, 69, 68,  2, 66, 89,  2, 53, 82, 73, 83, 72,  2,
        48,  8, 47, 69],
       [27, 56, 72, 65, 84,  2, 34, 73, 76, 83,  2, 58, 79, 85, 32,  1,
        51, 27, 68, 79],
       [92, 68, 70, 65,  2, 65, 71, 70, 92,  9, 69, 16, 70, 16, 71, 10,
        69,  2, 69, 70]])